In [2]:
from dataclasses import dataclass

@dataclass
class PropertyFinanceParams:
    """Tunable parameters that describe the finances of a property."""
    purchase_price: float
    deposit_amount: float
    loan_duration_years: int
    lmi_amount: float
    annual_rental_income: float
    annual_rental_growth_rate: float
    annual_interest_rate: float
    annual_growth_rate: float

In [3]:
def calculate_stamp_duty(purchase_price: float, first_home: bool) -> float:
    if first_home:
        if purchase_price < 600000:
            return 0
        elif purchase_price < 605000:
            return 1045
        elif purchase_price < 625000:
            return 5428
        elif purchase_price < 650000:
            return 11356
        elif purchase_price < 675000:
            return 17785
        elif purchase_price < 700000:
            return 24713
        elif purchase_price < 725000:
            return 32141
        elif purchase_price < 745000:
            return 38444
        else:
            return
    else:
        if purchase_price < 25000:
            return purchase_price * 0.014
        elif purchase_price < 130000:
            return 350 + (purchase_price - 25000) * 0.024
        elif purchase_price < 960000:
            return 2870 + (purchase_price - 130000) * 0.06
        elif purchase_price < 2000000:
            return purchase_price * 0.055
        else:
            return 110000 + (purchase_price - 2000000) * 0.065
        
def calculate_annual_repayments(principal: float, annual_interest_rate: float, loan_duration_years: int):
    return (principal * annual_interest_rate * (1 + annual_interest_rate) ** loan_duration_years) / ((1 + annual_interest_rate) ** loan_duration_years - 1)

In [4]:
def run_simulation(property_finance_params: PropertyFinanceParams):
    initial_loan_amount = property_finance_params.purchase_price - property_finance_params.deposit_amount
    yearly_loan_balance = [initial_loan_amount]

    stamp_duty = calculate_stamp_duty(property_finance_params.purchase_price, first_home=False)
    upfront_costs = stamp_duty + property_finance_params.deposit_amount + property_finance_params.lmi_amount

    print(f"Upfront Costs: {upfront_costs:.2f} = {property_finance_params.deposit_amount:.2f} deposit + {property_finance_params.lmi_amount:.2f} LMI + {stamp_duty:.2f} stamp duty")

    annual_mortgage_payment = calculate_annual_repayments(initial_loan_amount, property_finance_params.annual_interest_rate, 
                                                          property_finance_params.loan_duration_years)
    
    print(f"Annual Mortgage Payment: {annual_mortgage_payment:.2f}")

    yearly_interest_paid = []
    yearly_principal_paid = []
    yearly_property_value = [property_finance_params.purchase_price]
    yearly_rental_income = [property_finance_params.annual_rental_income]

    for year in range(property_finance_params.loan_duration_years):
        interest_paid = yearly_loan_balance[-1] * property_finance_params.annual_interest_rate
        yearly_interest_paid.append(interest_paid)
        yearly_principal_paid.append(annual_mortgage_payment - interest_paid)

        yearly_loan_balance.append(yearly_loan_balance[-1] - yearly_principal_paid[-1])

        yearly_property_value.append(yearly_property_value[-1] * (1 + property_finance_params.annual_growth_rate))

        yearly_rental_income.append(yearly_rental_income[-1] * (1 + property_finance_params.annual_rental_growth_rate))

        if yearly_loan_balance[-1] <= 0:
            break  # Loan fully paid off

    print()

    print(f"Total Paid: {annual_mortgage_payment * property_finance_params.loan_duration_years:.2f}")
    print(f"Property Value: {yearly_property_value[-1]:.2f}")
    print(f"Total Interest Paid: {sum(yearly_interest_paid):.2f}")
    print(f"Total Rental Income: {yearly_rental_income[-1]:.2f}")

    print()

    print(f"Total Paid (10yr): {annual_mortgage_payment * 10:.2f}")
    print(f"Property Value (10yr): {yearly_property_value[10]:.2f}")
    print(f"Total Interest Paid (10yr): {sum(yearly_interest_paid[:10]):.2f}")
    print(f"Total Principal Paid (10yr): {sum(yearly_principal_paid[:10]):.2f}")
    print(f"Total Rental Income (10yr): {sum(yearly_rental_income[:10]):.2f}")
    print(f"Net Cash Position (10yr): {sum(yearly_rental_income[:10]) - (annual_mortgage_payment * 10):.2f}")
    print(f"Loan Balance (10yr): {yearly_loan_balance[10]:.2f}")
    print(f"Total Equity (10yr): {yearly_property_value[10] - yearly_loan_balance[10]:.2f}")


run_simulation(
    PropertyFinanceParams(
        1300000,
        250000,
        30,
        0,
        36000,
        0.04,
        0.066,
        0.07)
)

Upfront Costs: 321500.00 = 250000.00 deposit + 0.00 LMI + 71500.00 stamp duty
Annual Mortgage Payment: 81241.59

Total Paid: 2437247.81
Property Value: 9895931.56
Total Interest Paid: 1387247.81
Total Rental Income: 116762.31

Total Paid (10yr): 812415.94
Property Value (10yr): 2557296.76
Total Interest Paid (10yr): 650510.03
Total Principal Paid (10yr): 161905.91
Total Rental Income (10yr): 432219.86
Net Cash Position (10yr): -380196.08
Loan Balance (10yr): 888094.09
Total Equity (10yr): 1669202.67
